In [1]:
from keras.models import Sequential
from keras.layers import *
from collections import deque
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import random

Using TensorFlow backend.


In [2]:
class Agent:
    
    def __init__(self, state_size=3, action_size=3):
        
        self.action_size = action_size
        self.state_size = state_size
        self.memory = deque(maxlen=2000)
        self.gamma = 0.95
        self.epsilon = 1.0
        self.epsilon_decay = 0.995
        self.epsilon_min = 0.01
        self.learning_rate = 0.001
        
        self.model = self._create_model_action_predict()
        
    def _create_model_action_predict(self):
        
        model = Sequential()
        model.add(LSTM(4,input_shape=(self.state_size,1), return_sequences=True))
        #model.add(Dropout(0.3))
        model.add(LSTM(4))
        model.add(Dropout(0.3))
        model.add(Dense(self.action_size, activation="softmax"))
        model.compile(loss="mean_squared_error", optimizer='adam', metrics=['acc'])
        
        return model
    
    def remember(self, state, action, reward, next_state, done):
        
        self.memory.append((state, action, reward, next_state, done))
        
    def act(self, state):
        
        if np.random.rand() <= self.epsilon:
            
            return random.randrange(self.action_size)
        
        return np.argmax(self.model.predict(state)[0])
    
    def train(self, batch_size=32):
        
        minibatch = random.sample(self.memory, batch_size)
        
        for experience in minibatch:
            
            state, action, reward, next_state, done = experience
            
            if not done:
                
                target = reward + self.gamma*np.amax(self.model.predict(next_state)[0])
                
            else:
                
                target = reward
                
            target_f = self.model.predict(state)
            target_f[0][action] = target
            
            self.model.fit(state, target_f, epochs=1, verbose=0)
            
        if self.epsilon > self.epsilon_min:
            
            self.epsilon *= self.epsilon_decay
            
    def load(self, name):
        self.model.load_weights(name)
        
    def save(self, name):
        self.model.save_weights(name)

In [3]:
n_episodes = 50
output_dir = 'trading_bot/'

done = False
state_size = 3
action_size = 3
batch_size = 32
agent = Agent(state_size, action_size)

In [4]:
import gym
import gym_trading_bot
env = gym.make('TradingBot-v0')

for e in range(n_episodes): # this game is won if we complete 200 episodes
    state = env.reset()
    state = np.reshape(state, [1,state_size,1]) 
    # We reshape it because we have to pass it to our neural network as an example
    
    for time in range(5000): # we choose a value higher than 200 as this game completes we if survive for 
                            # 200 time-steps
        env.render()
        action = agent.act(state)
        next_state,reward,done,other_info = env.step(action)
        reward = reward if not done else -10
        next_state = np.reshape(next_state,[1,state_size,1])
        agent.remember(state,action,reward,next_state,done) # Gaining Experience
        state = next_state
        
        if done:
            print("Game Episode :{}/{} High Score :{} Exploration Rate:{:.2}\n--------------------------------------".format(e+1,n_episodes,time,agent.epsilon))
            print("Profit: {}\nLoss: {}".format((max(0,(env.balance-env.initial_balance_b))), (min(0, (env.balance-env.initial_balance_b)))))
            break
            
    
    if len(agent.memory)>batch_size:
        agent.train(batch_size)
        
    # We will save our updated model weights every 50 game episodes
    if e%50 == 0:
        agent.save(output_dir+"weights_"+'{:04d}'.format(e)+".hdf5")
        
print("Deep Q-Learner Model Trained")
env.close()

[2020-03-22 13:55:08,366] Making new env: TradingBot-v0
/Users/pritichugh/opt/anaconda3/lib/python3.7/site-packages/gym/envs/registration.py:17: PkgResourcesDeprecationWarning: Parameters to load are deprecated.  Call .resolve and .require separately.
  result = entry_point.load(False)


Environment Created
Initail Balance: 500000
Initial Stock Volume held: 0
Initail Profit: 0
Step: 1
Balance: 500000
Stocks Volume: 0
Step: 2
Balance: 500000.0
Stocks Volume: 0
Step: 3
Balance: 500000.0
Stocks Volume: 0
Step: 4
Balance: 500000.0
Stocks Volume: 0
Step: 5
Balance: 500000.0
Stocks Volume: 0
Step: 6
Balance: 500000.0
Stocks Volume: 0
Step: 7
Balance: 185.43000000005122
Stocks Volume: 1867
Step: 8
Balance: 185.43000000005122
Stocks Volume: 1867
Step: 9
Balance: 185.43000000005122
Stocks Volume: 1867
Step: 10
Balance: 185.43000000005122
Stocks Volume: 1867
Step: 11
Balance: 185.43000000005122
Stocks Volume: 1867
Step: 12
Balance: 511071.31
Stocks Volume: 0
Step: 13
Balance: 511071.31
Stocks Volume: 0
Step: 14
Balance: 511071.31
Stocks Volume: 0
Step: 15
Balance: 20.520000000018626
Stocks Volume: 1877
Step: 16
Balance: 20.520000000018626
Stocks Volume: 1877
Step: 17
Balance: 20.520000000018626
Stocks Volume: 1877
Step: 18
Balance: 20.520000000018626
Stocks Volume: 1877
Step: 19

Stocks Volume: 0
Step: 950
Balance: 511480.89499999967
Stocks Volume: 0
Step: 951
Balance: 511480.89499999967
Stocks Volume: 0
Step: 952
Balance: 511480.89499999967
Stocks Volume: 0
Step: 953
Balance: 511480.89499999967
Stocks Volume: 0
Step: 954
Balance: 511480.89499999967
Stocks Volume: 0
Step: 955
Balance: 511480.89499999967
Stocks Volume: 0
Step: 956
Balance: 511480.89499999967
Stocks Volume: 0
Step: 957
Balance: 511480.89499999967
Stocks Volume: 0
Step: 958
Balance: 217.77499999967404
Stocks Volume: 1852
Step: 959
Balance: 217.77499999967404
Stocks Volume: 1852
Step: 960
Balance: 511332.7349999997
Stocks Volume: 0
Step: 961
Balance: 511332.7349999997
Stocks Volume: 0
Step: 962
Balance: 511332.7349999997
Stocks Volume: 0
Step: 963
Balance: 511332.7349999997
Stocks Volume: 0
Step: 964
Balance: 511332.7349999997
Stocks Volume: 0
Step: 965
Balance: 511332.7349999997
Stocks Volume: 0
Step: 966
Balance: 511332.7349999997
Stocks Volume: 0
Step: 967
Balance: 511332.7349999997
Stocks Volum

Step: 1
Balance: 500000
Stocks Volume: 0
Step: 2
Balance: 210.99599999998463
Stocks Volume: 1871
Step: 3
Balance: 210.99599999998463
Stocks Volume: 1871
Step: 4
Balance: 210.99599999998463
Stocks Volume: 1871
Step: 5
Balance: 210.99599999998463
Stocks Volume: 1871
Step: 6
Balance: 502913.7083
Stocks Volume: 0
Step: 7
Balance: 154.32830000005197
Stocks Volume: 1878
Step: 8
Balance: 502819.8083000001
Stocks Volume: 0
Step: 9
Balance: 502819.8083000001
Stocks Volume: 0
Step: 10
Balance: 502819.8083000001
Stocks Volume: 0
Step: 11
Balance: 230.1083000000217
Stocks Volume: 1842
Step: 12
Balance: 504274.98829999997
Stocks Volume: 0
Step: 13
Balance: 1.308299999916926
Stocks Volume: 1838
Step: 14
Balance: 1.308299999916926
Stocks Volume: 1838
Step: 15
Balance: 1.308299999916926
Stocks Volume: 1838
Step: 16
Balance: 1.308299999916926
Stocks Volume: 1838
Step: 17
Balance: 1.308299999916926
Stocks Volume: 1838
Step: 18
Balance: 501940.72829999984
Stocks Volume: 0
Step: 19
Balance: 40.84829999983

Stocks Volume: 1859
Step: 873
Balance: 512408.18569999916
Stocks Volume: 0
Step: 874
Balance: 512408.18569999916
Stocks Volume: 0
Step: 875
Balance: 512408.18569999916
Stocks Volume: 0
Step: 876
Balance: 51.700499999162275
Stocks Volume: 1862
Step: 877
Balance: 512922.28389999917
Stocks Volume: 0
Step: 878
Balance: 512922.28389999917
Stocks Volume: 0
Step: 879
Balance: 512922.28389999917
Stocks Volume: 0
Step: 880
Balance: 27.283899999165442
Stocks Volume: 1860
Step: 881
Balance: 27.283899999165442
Stocks Volume: 1860
Step: 882
Balance: 27.283899999165442
Stocks Volume: 1860
Step: 883
Balance: 513749.9838999992
Stocks Volume: 0
Step: 884
Balance: 103.78389999910723
Stocks Volume: 1857
Step: 885
Balance: 103.78389999910723
Stocks Volume: 1857
Step: 886
Balance: 513811.6362999991
Stocks Volume: 0
Step: 887
Balance: 513811.6362999991
Stocks Volume: 0
Step: 888
Balance: 513811.6362999991
Stocks Volume: 0
Step: 889
Balance: 513811.6362999991
Stocks Volume: 0
Step: 890
Balance: 513811.636299

...

Step: 371
Balance: 484149.95219999965
Stocks Volume: 0
Step: 372
Balance: 484149.95219999965
Stocks Volume: 0
Step: 373
Balance: 484149.95219999965
Stocks Volume: 0
Step: 374
Balance: 484149.95219999965
Stocks Volume: 0
Step: 375
Balance: 484149.95219999965
Stocks Volume: 0
Step: 376
Balance: 152.79069999966305
Stocks Volume: 1735
Step: 377
Balance: 152.79069999966305
Stocks Volume: 1735
Step: 378
Balance: 481424.4406999996
Stocks Volume: 0
Step: 379
Balance: 481424.4406999996
Stocks Volume: 0
Step: 380
Balance: 481424.4406999996
Stocks Volume: 0
Step: 381
Balance: 481424.4406999996
Stocks Volume: 0
Step: 382
Balance: 17.320699999574572
Stocks Volume: 1746
Step: 383
Balance: 480664.9306999996
Stocks Volume: 0
Step: 384
Balance: 480664.9306999996
Stocks Volume: 0
Step: 385
Balance: 22.720699999656063
Stocks Volume: 1739
Step: 386
Balance: 482059.9564999997
Stocks Volume: 0
Step: 387
Balance: 482059.9564999997
Stocks Volume: 0
Step: 388
Balance: 482059.9564999997
Stocks Volume: 0
Step: 3

Step: 792
Balance: 515879.6478999992
Stocks Volume: 0
Step: 793
Balance: 515879.6478999992
Stocks Volume: 0
Step: 794
Balance: 515879.6478999992
Stocks Volume: 0
Step: 795
Balance: 515879.6478999992
Stocks Volume: 0
Step: 796
Balance: 515879.6478999992
Stocks Volume: 0
Step: 797
Balance: 515879.6478999992
Stocks Volume: 0
Step: 798
Balance: 515879.6478999992
Stocks Volume: 0
Step: 799
Balance: 515879.6478999992
Stocks Volume: 0
Step: 800
Balance: 515879.6478999992
Stocks Volume: 0
Step: 801
Balance: 515879.6478999992
Stocks Volume: 0
Step: 802
Balance: 171.72789999924134
Stocks Volume: 1852
Step: 803
Balance: 515694.2626999992
Stocks Volume: 0
Step: 804
Balance: 515694.2626999992
Stocks Volume: 0
Step: 805
Balance: 515694.2626999992
Stocks Volume: 0
Step: 806
Balance: 515694.2626999992
Stocks Volume: 0
Step: 807
Balance: 515694.2626999992
Stocks Volume: 0
Step: 808
Balance: 261.92969999922207
Stocks Volume: 1853
Step: 809
Balance: 515395.9296999992
Stocks Volume: 0
Step: 810
Balance: 5

Step: 1196
Balance: 528299.9407999994
Stocks Volume: 0
Step: 1197
Balance: 528299.9407999994
Stocks Volume: 0
Step: 1198
Balance: 116.9007999994792
Stocks Volume: 2024
Step: 1199
Balance: 529979.8607999996
Stocks Volume: 0
Step: 1200
Balance: 104.59079999953974
Stocks Volume: 2025
Step: 1201
Balance: 527981.5907999995
Stocks Volume: 0
Step: 1202
Balance: 527981.5907999995
Stocks Volume: 0
Step: 1203
Balance: 527981.5907999995
Stocks Volume: 0
Step: 1204
Balance: 527981.5907999995
Stocks Volume: 0
Step: 1205
Balance: 527981.5907999995
Stocks Volume: 0
Step: 1206
Balance: 214.3223999995971
Stocks Volume: 2034
Step: 1207
Balance: 214.3223999995971
Stocks Volume: 2034
Step: 1208
Balance: 527427.1223999995
Stocks Volume: 0
Step: 1209
Balance: 225.28239999955986
Stocks Volume: 2036
Step: 1210
Balance: 528485.8423999995
Stocks Volume: 0
Step: 1211
Balance: 528485.8423999995
Stocks Volume: 0
Step: 1212
Balance: 528485.8423999995
Stocks Volume: 0
Step: 1213
Balance: 528485.8423999995
Stocks Vol

Step: 1511
Balance: 517969.4000999992
Stocks Volume: 0
Step: 1512
Balance: 517969.4000999992
Stocks Volume: 0
Step: 1513
Balance: 517969.4000999992
Stocks Volume: 0
Step: 1514
Balance: 517969.4000999992
Stocks Volume: 0
Step: 1515
Balance: 517969.4000999992
Stocks Volume: 0
Step: 1516
Balance: 225.10009999916656
Stocks Volume: 2026
Step: 1517
Balance: 225.10009999916656
Stocks Volume: 2026
Step: 1518
Balance: 225.10009999916656
Stocks Volume: 2026
Step: 1519
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1520
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1521
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1522
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1523
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1524
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1525
Balance: 507657.0600999992
Stocks Volume: 0
Step: 1526
Balance: 86.31009999918751
Stocks Volume: 1915
Step: 1527
Balance: 86.31009999918751
Stocks Volume: 1915
Step: 1528
Balance: 86.31009999918751
Stocks Vo

Step: 1888
Balance: 504895.948499999
Stocks Volume: 0
Step: 1889
Balance: 504895.948499999
Stocks Volume: 0
Step: 1890
Balance: 504895.948499999
Stocks Volume: 0
Step: 1891
Balance: 6.598499998974148
Stocks Volume: 1871
Step: 1892
Balance: 6.598499998974148
Stocks Volume: 1871
Step: 1893
Balance: 505083.0484999989
Stocks Volume: 0
Step: 1894
Balance: 505083.0484999989
Stocks Volume: 0
Step: 1895
Balance: 505083.0484999989
Stocks Volume: 0
Game Episode :50/50 High Score :1894 Exploration Rate:0.78
--------------------------------------
Profit: 5083.048499998928
Loss: 0
Deep Q-Learner Model Trained
Step: 1896
Balance: 505083.0484999989
Stocks Volume: 0


In [1]:
import gym

In [2]:
import gym_trading_bot

In [3]:
env = gym.make('TradingBot-v0')

[2020-03-22 11:07:26,358] Making new env: TradingBot-v0
/Users/pritichugh/opt/anaconda3/lib/python3.7/site-packages/gym/envs/registration.py:17: PkgResourcesDeprecationWarning: Parameters to load are deprecated.  Call .resolve and .require separately.
  result = entry_point.load(False)


Environment Created
Initail Balance: 500000
Initial Stock Volume held: 0
Initail Profit: 0


In [4]:
init_state = env.reset()
print("Initial State:{}".format(init_state))

Initial State:[263.75  266.19  267.124]


In [5]:
action = env.action_space.sample()
print(action)

0


In [6]:
observation,reward,done,other_info = env.step(action)
print("Observation:{}\nReward:{}\nDone:{}\nInfo:{}".format(observation,reward,done,other_info))

267.124
1871
1871
500000
210.99599999998463
Observation:[266.19  267.124 267.89 ]
Reward:2.0
Done:False
Info:{}


In [9]:
print(env.loss)
print(env.profit)
print(env.balance)
print(env.stock_volume_aquired)

499789.004
0
210.99599999998463
1871
